In [ ]:
import pandas as pd
import requests
from io import StringIO
import json
import branca.colormap as cm
import numpy as np

# ==============================================================================
# Step 1: Fetch the master station list
# ==============================================================================
stations_url = "https://data.geo.admin.ch/ch.meteoschweiz.messnetz-automatisch/ch.meteoschweiz.messnetz-automatisch_en.csv"
print(f"Fetching master station list...")
try:
    df_stations = pd.read_csv(stations_url, sep=';', skiprows=0, encoding='latin1')
    df_stations.columns = df_stations.columns.str.strip()
except Exception as e:
    print(f"Fatal error: Could not load the master station list. {e}")
    exit()

# ==============================================================================
# Step 2: Process station data
# ==============================================================================
all_daily_averages = []
print("--- Starting Pass 1: Processing data for all stations ---")

for index, station in df_stations.iterrows():
    try:
        abbr = station['Abbr.']
        lat = station['Latitude']
        lon = station['Longitude']
        station_name = station['Station']
        altitude = station['Station height m a. sea level']
    except KeyError as e:
        print(f"Warning: Missing column {e} in station list. Skipping row.")
        continue
    if pd.isna(lat) or pd.isna(lon) or pd.isna(altitude):
        continue
    abbr_lower = abbr.lower()
    hist_url = f"https://data.geo.admin.ch/ch.meteoschweiz.ogd-smn/{abbr_lower}/ogd-smn_{abbr_lower}_h_historical_2010-2019.csv"
    print(f"-> Processing {abbr}...")
    try:
        response = requests.get(hist_url, timeout=15)
        response.raise_for_status()
        df_data = pd.read_csv(StringIO(response.text), sep=';', usecols=['reference_timestamp', 'tre005h0', 'tre200h0', 'htoauths'], low_memory=False)
        
        df_data['temp'] = df_data['tre005h0'].fillna(df_data['tre200h0'])
        df_data['time'] = pd.to_datetime(df_data['reference_timestamp'], format='%d.%m.%Y %H:%M', errors='coerce')
        df_data['temp'] = pd.to_numeric(df_data['temp'], errors='coerce')
        df_data['snow_height_cm'] = pd.to_numeric(df_data['htoauths'], errors='coerce')
        
        # ==================================================================
        # Clip negative snow values to zero.
        # This treats sensor artifacts (small negative values) as "real zero" measurements.
        df_data['snow_height_cm'] = df_data['snow_height_cm'].clip(lower=0)
        # ==================================================================
        
        df_data = df_data.dropna(subset=['time', 'temp'])
        if df_data.empty: continue
            
        daily_averages = df_data.groupby([df_data['time'].dt.month.rename('month'), df_data['time'].dt.day.rename('day')]).agg(
            avg_temp=('temp', 'mean'),
            avg_snow=('snow_height_cm', 'mean')
        ).reset_index()

        for _, row in daily_averages.iterrows():
            avg_snow_val = None if pd.isna(row['avg_snow']) else row['avg_snow']
            all_daily_averages.append({
                "lat": lat, "lon": lon, "station_name": station_name,
                "abbr": abbr, "month": row['month'], "day": row['day'], 
                "avg_temp": row['avg_temp'],
                "avg_snow": avg_snow_val,
                "altitude": altitude
            })
    except Exception as e:
        print(f"  - Could not process {abbr}. Reason: {e}")
        continue

if not all_daily_averages:
    print("\nCRITICAL: No data could be processed.")
    exit()
    

In [ ]:
# ==============================================================================
# Step 3, 4: Colormaps, Features
# ==============================================================================

print("\n--- Processing complete. Generating features. ---")
df_all_data = pd.DataFrame(all_daily_averages)

min_temp, max_temp = df_all_data['avg_temp'].min(), df_all_data['avg_temp'].max()
temp_colors = ['#480074', '#00008B', '#ADD8E6', '#FFFF00', '#FFA500', '#FF0000', '#8B0000']
temp_index = [min_temp, min_temp * 0.5, 0, 1e-6, max_temp * 0.33, max_temp * 0.66, max_temp]
temp_colormap = cm.LinearColormap(colors=temp_colors, index=temp_index, vmin=min_temp, vmax=max_temp)

max_snow_val = df_all_data['avg_snow'].dropna().max()
snow_vmax = max_snow_val if pd.notna(max_snow_val) and max_snow_val > 0 else 1.0
snow_thresholds = {
    0: '#cccccc',    # Grey for real zero
    1: '#d9f0a3',    # Lightest green
    10: '#78c679',   # Light-medium green
    50: '#238443',   # Medium green
    100: '#004529'   # Darkest green
}
points_of_interest = set(snow_thresholds.keys())
points_of_interest.add(snow_vmax)
snow_index = sorted([p for p in points_of_interest if p <= snow_vmax])
snow_colors = []
for val in snow_index:
    color_key = max([k for k in snow_thresholds.keys() if k <= val])
    snow_colors.append(snow_thresholds[color_key])
snow_colormap = cm.LinearColormap(colors=snow_colors, index=snow_index, vmin=0, vmax=snow_vmax)

features = []
for index, row in df_all_data.iterrows():
    feature_time = f"2020-{int(row['month']):02d}-{int(row['day']):02d}T12:00:00"
    fill_color = temp_colormap(row['avg_temp'])
    snow_val = row['avg_snow']
    if pd.isna(snow_val):
        stroke_color = 'transparent'
        snow_text = "Avg snow: No measurement"
        snow_for_json = None
    elif snow_val == 0:
        stroke_color = snow_thresholds[0]
        snow_text = f"Avg snow: {snow_val:.1f} cm"
        snow_for_json = 0
    else:
        stroke_color = snow_colormap(snow_val)
        snow_text = f"Avg snow: {snow_val:.1f} cm"
        snow_for_json = snow_val
    popup_html = (f"<b>{row['station_name']} ({row['abbr']})</b><br>"
                  f"Avg temp: {row['avg_temp']:.1f}°C<br>"
                  f"{snow_text}")
    features.append({
        'type': 'Feature',
        'geometry': {'type': 'Point', 'coordinates': [round(row['lon'], 4), round(row['lat'], 4)]},
        'properties': {
            'time': feature_time, 'popup': popup_html, 'icon': 'circle',
            'iconstyle': {
                'fillColor': fill_color, 'fillOpacity': 0.8, 'color': stroke_color,
                'weight': 8, 'radius': 12
            },
            'altitude': row['altitude'], 'temp': row['avg_temp'], 'snow': snow_for_json
        }
    })
geojson_data = {'type': 'FeatureCollection', 'features': features}

def create_legend_html(colormap, title, unit, is_snow=False):
    header = f'<strong>{title} ({unit})</strong><br>'
    if is_snow:
        header += f'<i style="background:transparent; border: 2px solid {snow_thresholds[0]};"></i> Real Zero<br>'
    items = []
    start_index = 1 if is_snow and colormap.index[0] == 0 else 0
    printed_labels = set()
    for i in range(start_index, len(colormap.index)):
        val = colormap.index[i]
        label = f'{val:.0f}'
        if label not in printed_labels:
            color = colormap.colors[i]
            items.append(f'<i style="background:{color}"></i> {label}<br>')
            printed_labels.add(label)
    return header + ''.join(items)

In [ ]:
# ==============================================================================
# Step 5: Generate Legend HTML
# ==============================================================================

# --- Temperature Legend ---
temp_items = []
for val in temp_colormap.index:
    color_hex = temp_colormap(val) # Explicitly call the colormap to get the hex color
    temp_items.append(
        '<div class="legend-horizontal-item">'
        f'<div class="legend-horizontal-box" style="background-color:{color_hex}; border: 1px solid #777;"></div>'
        f'<div class="legend-horizontal-label">{int(val)}</div>'
        '</div>'
    )
temp_legend_html = '<strong>Temperature (°C)</strong><div class="legend-horizontal-container">{}</div>'.format("".join(temp_items))

# --- Snow Legend ---
snow_items = []
legend_points = sorted(list(snow_thresholds.keys()))
if max_snow_val > legend_points[-1]:
    legend_points.append(int(max_snow_val))

for val in legend_points:
    color_hex = snow_colormap(val)
    # Special style for the "Real Zero" box
    if val == 0:
        style = f'background-color:transparent; border: 2px solid {color_hex};'
    else:
        style = f'background-color:{color_hex}; border: 1px solid #777;'
        
    snow_items.append(
        '<div class="legend-horizontal-item">'
        f'<div class="legend-horizontal-box" style="{style}"></div>'
        f'<div class="legend-horizontal-label">{val}</div>'
        '</div>'
    )
snow_legend_html = '<strong>Snow Height (Stroke) (cm)</strong><div class="legend-horizontal-container">{}</div>'.format("".join(snow_items))

legend_html_content = f"""
<div class="legend-section">{temp_legend_html}</div>
<hr>
<div class="legend-section">{snow_legend_html}</div>
<div class="legend-section" style="line-height: 1.2; margin-top: 5px;">Stations with no snow sensor (or no border) did not provide a measurement.</div>
"""

# ==============================================================================
# Step 6: Save the data and the HTML shell
# ==============================================================================
with open('data.json', 'w') as f:
    json.dump(geojson_data, f)
print("\nSuccessfully saved GeoJSON data to data.json")

with open("map.html", "w", encoding="utf-8") as f:
    f.write(f"""<!DOCTYPE html>
<html><head>
    <title>Swiss Temperature & Snow Map</title>
    <meta charset="utf-8" /><meta name="viewport" content="width=device-width, initial-scale=1.0">
    <script src="https://cdn.jsdelivr.net/npm/leaflet@1.9.3/dist/leaflet.js"></script>
    <script src="https://code.jquery.com/jquery-1.12.4.min.js"></script>
    <script src="https://cdnjs.cloudflare.com/ajax/libs/moment.js/2.18.1/moment.min.js"></script>
    <script src="https://cdn.jsdelivr.net/npm/iso8601-js-period@0.2.1/iso8601.min.js"></script>
    <script src="https://cdn.jsdelivr.net/npm/leaflet-timedimension@1.1.1/dist/leaflet.timedimension.min.js"></script>
    <script src="https://cdn.jsdelivr.net/npm/chart.js"></script>
    <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/leaflet@1.9.3/dist/leaflet.css"/>
    <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/leaflet-timedimension@1.1.1/dist/leaflet.timedimension.control.css"/>
    <style>
        html, body, #map {{ width: 100%; height: 100%; margin: 0; padding: 0; }}
        .plot-container {{ position: absolute; right: 10px; width: 400px; background-color: rgba(255, 255, 255, 0.85); border: 1px solid #ccc; border-radius: 5px; z-index: 900; padding: 10px; }}
        #temp-plot-container {{ bottom: 260px; height: 200px; }}
        #snow-plot-container {{ bottom: 40px; height: 200px; }}
        .legend {{ padding: 6px 8px; font: 12px Arial, Helvetica, sans-serif; background: rgba(255,255,255,0.8); box-shadow: 0 0 15px rgba(0,0,0,0.2); border-radius: 5px; line-height: 18px; color: #555; max-width: 300px; }}
        .legend .legend-section {{ margin: 4px 0; }}
        .legend hr {{ border-top: 1px solid #ddd; margin: 5px 0; }}
        .legend-horizontal-container {{ display: flex; flex-wrap: wrap; align-items: center; white-space: normal; margin-top: 5px; }}
        .legend-horizontal-item {{ display: flex; align-items: center; margin-right: 5px; margin-bottom: 2px; }}
        /* MODIFIED: Removed border from class to ensure inline style takes precedence */
        .legend-horizontal-box {{ width: 20px; height: 15px; box-sizing: border-box; flex-shrink: 0; }}
        .legend-horizontal-label {{ margin-left: 3px; font-size: 10px; }}
    </style>
</head><body>
    <div id="map"></div>
    <div id="temp-plot-container" class="plot-container"><canvas id="temp-altitude-chart"></canvas></div>
    <div id="snow-plot-container" class="plot-container"><canvas id="snow-altitude-chart"></canvas></div>
    <script>
        var map = L.map('map').setView([46.8182, 8.2275], 9);
        L.tileLayer('https://{{s}}.tile.openstreetmap.org/{{z}}/{{x}}/{{y}}.png', {{ attribution: '© <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors. Weather Source: MeteoSchweiz.' }}).addTo(map);
        const tempCtx = document.getElementById('temp-altitude-chart').getContext('2d');
        const tempScatterChart = new Chart(tempCtx, {{ type: 'scatter', data: {{ datasets: [{{ label: 'Temp vs. Altitude', data: [], borderWidth: 1 }}] }}, options: {{ responsive: true, maintainAspectRatio: false, scales: {{ x: {{ type: 'linear', position: 'bottom', title: {{ display: true, text: 'Altitude (m)' }} }}, y: {{ title: {{ display: true, text: 'Temperature (°C)' }} }} }} }} }});
        const snowCtx = document.getElementById('snow-altitude-chart').getContext('2d');
        const snowScatterChart = new Chart(snowCtx, {{ type: 'scatter', data: {{ datasets: [{{ label: 'Snow Height vs. Altitude', data: [], borderWidth: 1, backgroundColor: '#238443', borderColor: '#238443' }}] }}, options: {{ responsive: true, maintainAspectRatio: false, scales: {{ x: {{ type: 'linear', position: 'bottom', title: {{ display: true, text: 'Altitude (m)' }} }}, y: {{ title: {{ display: true, text: 'Avg Snow Height (cm)' }} }} }} }} }});
        var legend = L.control({{position: 'topright'}});
        legend.onAdd = function (map) {{ var div = L.DomUtil.create('div', 'info legend'); div.innerHTML = `{legend_html_content}`; return div; }};
        legend.addTo(map);
        var dataByDate = new Map();
        fetch('data.json').then(response => response.json()).then(data => {{
            data.features.forEach(feature => {{
                const dateKey = feature.properties.time.substring(0, 10);
                if (!dataByDate.has(dateKey)) {{ dataByDate.set(dateKey, []); }}
                dataByDate.get(dateKey).push({{ altitude: feature.properties.altitude, temp: feature.properties.temp, snow: feature.properties.snow, color: feature.properties.iconstyle.fillColor }});
            }});
            var geoJsonLayer = L.geoJson(data, {{ pointToLayer: (f, l) => L.circleMarker(l, f.properties.iconstyle), onEachFeature: (f, l) => l.bindPopup(f.properties.popup) }});
            var timeDimensionLayer = L.timeDimension.layer.geoJson(geoJsonLayer, {{ updateTimeDimension: true, addlastPoint: true }});
            var timeDimensionControl = L.control.timeDimension({{ period: "P1D", playerOptions: {{ transitionTime: 250, loop: false, startOver: true }} }});
            map.timeDimension = L.timeDimension();
            map.addControl(timeDimensionControl);
            timeDimensionLayer.addTo(map);
            map.timeDimension.on('timeload', function(e) {{
                const dateKey = new Date(e.time).toISOString().substring(0, 10);
                const currentData = dataByDate.get(dateKey) || [];
                const tempPlotData = currentData.map(d => ({{ x: d.altitude, y: d.temp }}));
                const tempPlotColors = currentData.map(d => d.color);
                tempScatterChart.data.datasets[0].data = tempPlotData;
                tempScatterChart.data.datasets[0].backgroundColor = tempPlotColors;
                tempScatterChart.data.datasets[0].borderColor = tempPlotColors;
                tempScatterChart.update('none');
                const snowPlotData = currentData.filter(d => d.snow > 0).map(d => ({{ x: d.altitude, y: d.snow }}));
                snowScatterChart.data.datasets[0].data = snowPlotData;
                snowScatterChart.update('none');
            }});
            const firstDateKey = dataByDate.keys().next().value;
            if (firstDateKey) {{ map.timeDimension.setCurrentTime(new Date(firstDateKey).getTime()); }}
        }}).catch(error => console.error('Error loading or processing GeoJSON data:', error));
    </script>
</body></html>""")

print("\nSuccessfully saved files.")
print("\n--- INSTRUCTIONS ---")
print("1. Run this new Python script.")
print("2. Run your local web server: python -m http.server")
print("3. Open your browser to: http://localhost:8000/map.html")